## Read in data 

In [1]:
import pandas as pd
import numpy as np
import json
import re
import spacy as sp

data = json.loads(open('data.json').read())

situations = data['situations']
for situation in situations:
    print(situation)

{'id': 11321, 'uuid': 'c8f256f2-f36e-449c-ae2b-3fef3561495d', 'changed': '2024-01-25T10:25:08+01:00', 'title': 'Mijn kind heeft eczeem', 'link': 'https://www.thuisarts.nl/eczeem/mijn-kind-heeft-eczeem', 'revision_date': '2020-04-16', 'subject': {'id': '11314', 'changed': '2024-01-25T10:25:08+01:00', 'title': 'Eczeem', 'link': 'https://www.thuisarts.nl/eczeem'}, 'content': [{'index': 0, 'type': 'text', 'category': 'In het kort', 'uuid': 'd86388f2-bb6b-4ebe-b451-bad201ea87c0', 'item': [{'title': 'In het kort', 'value': '<ul><li>Bij eczeem heeft uw kind een jeukende huid, met schilfers, bultjes, kloofjes of korstjes.</li>\n\t<li>Het zit vooral in het gezicht, op het hoofd,\xa0in de ellebogen en knieholten, op de polsen en enkels.</li>\n\t<li>Wassen met water en zeep maakt de klachten erger.</li>\n\t<li>2 of 3 keer per week douchen/baden is genoeg. Het liefst zonder zeep.</li>\n\t<li>Smeer uw kind elke dag in met een zalf of crème, zoals lanette creme.\xa0</li>\n\t<li>Soms is een zalf of c

## Extract text from situations

In [2]:
for situation in situations:
    title = situation['title']
    
    for content_item in situation['content']:
        content_category = content_item['category']
        
        for item in content_item['item']:
            item_title = item['title']
            item_value = item.get('value', None)
            
            if item_value is not None:
                print(f"Title: {title}\nCategory: {content_category}\nItem Title: {item_title}\nItem Value: {item_value}\n")

Title: Mijn kind heeft eczeem
Category: In het kort
Item Title: In het kort
Item Value: <ul><li>Bij eczeem heeft uw kind een jeukende huid, met schilfers, bultjes, kloofjes of korstjes.</li>
	<li>Het zit vooral in het gezicht, op het hoofd, in de ellebogen en knieholten, op de polsen en enkels.</li>
	<li>Wassen met water en zeep maakt de klachten erger.</li>
	<li>2 of 3 keer per week douchen/baden is genoeg. Het liefst zonder zeep.</li>
	<li>Smeer uw kind elke dag in met een zalf of crème, zoals lanette creme. </li>
	<li>Soms is een zalf of crème met hormonen erin nodig.</li>
</ul>

Title: Mijn kind heeft eczeem
Category: Wat is het
Item Title: Wat is eczeem bij kinderen?
Item Value: <p>Bij eczeem zitten er jeukende plekken op de huid, met schilfers, bultjes, kloofjes of korstjes. Bij een lichte huid zijn de plekken rood. Bij een getinte of donkere huid zijn het donkere plekken. </p>

<p>Eczeem bij kinderen komt vaak door erfelijke aanleg. De medische naam hiervoor is constitutioneel e

In [3]:
item_values = []

with open('nlp_data.txt', 'w', encoding='utf-8') as file:
    for situation in situations:
        title = situation['title']
        file.write(f"Situation: {title}\n\n")
        
        for content_item in situation['content']:
            content_category = content_item['category']
            
            for item in content_item['item']:
                item_title = item['title']
                
                #sometimes there is no 'value' because there is no text, only a video
                item_value = item.get('value', None) 
                
                if item_value is not None:
                    item_values.append(item_value)
                    file.write(f"Category: {content_category}\nCategory Title: {item_title}\nItem Value: {item_value}\n\n")


In [4]:
with open('nlp_data.txt', 'r', encoding='utf-8') as file:
    lines = file.readlines()

    situation_count = 0

    print_lines = True

    for line in lines:
        # Check if the line contains 'Situation:' and increment the count
        if 'Situation:' in line:
            situation_count += 1

        # Update print_lines flag
        if situation_count == 2:
            print_lines = False

        # Print the line if the flag is True
        if print_lines:
            print(line.strip())

Situation: Mijn kind heeft eczeem

Category: In het kort
Category Title: In het kort
Item Value: <ul><li>Bij eczeem heeft uw kind een jeukende huid, met schilfers, bultjes, kloofjes of korstjes.</li>
<li>Het zit vooral in het gezicht, op het hoofd, in de ellebogen en knieholten, op de polsen en enkels.</li>
<li>Wassen met water en zeep maakt de klachten erger.</li>
<li>2 of 3 keer per week douchen/baden is genoeg. Het liefst zonder zeep.</li>
<li>Smeer uw kind elke dag in met een zalf of crème, zoals lanette creme. </li>
<li>Soms is een zalf of crème met hormonen erin nodig.</li>
</ul>

Category: Wat is het
Category Title: Wat is eczeem bij kinderen?
Item Value: <p>Bij eczeem zitten er jeukende plekken op de huid, met schilfers, bultjes, kloofjes of korstjes. Bij een lichte huid zijn de plekken rood. Bij een getinte of donkere huid zijn het donkere plekken. </p>

<p>Eczeem bij kinderen komt vaak door erfelijke aanleg. De medische naam hiervoor is constitutioneel eczeem.  </p>

<p>Het b

In [5]:
#delete all html tags and special characters
tag_pattern = re.compile(r'<.*?>')
remove_pattern = re.compile(r'[\xa0\n\t]')

text = [remove_pattern.sub('', tag_pattern.sub('', item)) for item in item_values]

#make sure there is a space after each comma and period (for readability)
pattern = re.compile(r'(?<=[,.])(?=[^\s])')

text = [pattern.sub(r' ', sentence) for sentence in text]

#text should be a string of all the text
text = ' '.join(text)
print(text)

Bij eczeem heeft uw kind een jeukende huid, met schilfers, bultjes, kloofjes of korstjes. Het zit vooral in het gezicht, op het hoofd, in de ellebogen en knieholten, op de polsen en enkels. Wassen met water en zeep maakt de klachten erger. 2 of 3 keer per week douchen/baden is genoeg. Het liefst zonder zeep. Smeer uw kind elke dag in met een zalf of crème, zoals lanette creme. Soms is een zalf of crème met hormonen erin nodig. Bij eczeem zitten er jeukende plekken op de huid, met schilfers, bultjes, kloofjes of korstjes. Bij een lichte huid zijn de plekken rood. Bij een getinte of donkere huid zijn het donkere plekken. Eczeem bij kinderen komt vaak door erfelijke aanleg. De medische naam hiervoor is constitutioneel eczeem. Het begint vaak al bij baby's, soms al 3 maanden na de geboorte. Eczeem is niet vies of besmettelijk. Elkaar aanraken en knuffelen is belangrijk en kan zeker geen kwaad. Kinderen met eczeem hebben:jeukrode of donkere plekken op de huid, met schilfers, bultjes, blaasj

In [6]:
#tokenize, postag and parse text
nlp = sp.load('nl_core_news_sm')
doc = nlp(text)
for token in doc:
    print(token.text, token.pos_, token.dep_)
#it states that "moedervlekken" is a VERB, but it is a NOUN

#delete prepositions and stop words, and punctuation and lemmatize tokens (to get canonical form)
lemmas = [token.lemma_ for token in doc if not token.is_stop and not token.is_punct and not token.pos_ == 'ADP']

#lemmatization does not work well because it abbreviates "ellebogen" to "ellebog" and "polsen" to "pol", etc. "lanetten" becomes "laneten"

#give me all adjacent pairs of words
pairs = []
for i in range(len(lemmas)-1):
    pairs.append((lemmas[i], lemmas[i+1]))
print(pairs)

Bij ADP case
eczeem NOUN obl
heeft AUX aux
uw PRON nmod:poss
kind NOUN nsubj
een DET det
jeukende VERB amod
huid NOUN ROOT
, PUNCT punct
met ADP case
schilfers NOUN nmod
, PUNCT punct
bultjes NOUN conj
, PUNCT punct
kloofjes NOUN conj
of CCONJ cc
korstjes NOUN conj
. PUNCT punct
Het PRON nsubj
zit VERB ROOT
vooral ADV amod
in ADP case
het DET det
gezicht NOUN obl
, PUNCT punct
op ADP case
het DET det
hoofd NOUN nmod
, PUNCT punct
in ADP case
de DET det
ellebogen NOUN conj
en CCONJ cc
knieholten NOUN conj
, PUNCT punct
op ADP case
de DET det
polsen NOUN obl
en CCONJ cc
enkels NOUN conj
. PUNCT punct
Wassen ADJ nsubj
met ADP case
water NOUN nmod
en CCONJ cc
zeep NOUN conj
maakt VERB ROOT
de DET det
klachten NOUN obj
erger ADJ xcomp
. PUNCT punct
2 NUM nummod
of CCONJ cc
3 NUM conj
keer NOUN obl
per ADP case
week NOUN nmod
douchen/baden PROPN nmod
is AUX cop
genoeg ADV ROOT
. PUNCT punct
Het DET ROOT
liefst ADV fixed
zonder ADP case
zeep NOUN nmod
. PUNCT punct
Smeer VERB ROOT
uw PRON nmo